Example 11 - Example of rotor connected by a flexible mechanical coupling with parallel, agular or combined misalignment.
=====
In this example, we use the rotor seen in Example 10 for demonstrating the results obtained when we have a misalignment fault present in the system. 

In [1]:
import numpy as np

import ross as rs
from ross.faults import *
from ross.units import Q_
from ross.probe import Probe

# Make sure the default renderer is set to 'notebook' for inline plots in Jupyter
import plotly.io as pio

pio.renderers.default = "notebook"

In [2]:
"""Create example rotor with given number of elements."""
steel2 = rs.Material(name="Steel", rho=7850, E=2.17e11, G_s=81.2e9)
#  Rotor with 6 DoFs, with internal damping, with 10 shaft elements, 2 disks and 2 bearings.
i_d = 0
o_d = 0.019
n = 33

# fmt: off
L = np.array(
        [0  ,  25,  64, 104, 124, 143, 175, 207, 239, 271,
         303, 335, 345, 355, 380, 408, 436, 466, 496, 526,
         556, 586, 614, 647, 657, 667, 702, 737, 772, 807,
         842, 862, 881, 914]
         )/ 1000
# fmt: on

L = [L[i] - L[i - 1] for i in range(1, len(L))]

shaft_elem = [
    rs.ShaftElement(
        material=steel2,
        L=l,
        idl=i_d,
        odl=o_d,
        idr=i_d,
        odr=o_d,
        alpha=8.0501,
        beta=1.0e-5,
        rotary_inertia=True,
        shear_effects=True,
    )
    for l in L
]

Id = 0.003844540885417
Ip = 0.007513248437500

disk0 = rs.DiskElement(n=12, m=2.6375, Id=Id, Ip=Ip)
disk1 = rs.DiskElement(n=24, m=2.6375, Id=Id, Ip=Ip)

kxx1 = 4.40e5
kyy1 = 4.6114e5
kzz = 0
cxx1 = 27.4
cyy1 = 2.505
czz = 0
kxx2 = 9.50e5
kyy2 = 1.09e8
cxx2 = 50.4
cyy2 = 100.4553

bearing0 = rs.BearingElement(
    n=4, kxx=kxx1, kyy=kyy1, cxx=cxx1, cyy=cyy1, kzz=kzz, czz=czz
)
bearing1 = rs.BearingElement(
    n=31, kxx=kxx2, kyy=kyy2, cxx=cxx2, cyy=cyy2, kzz=kzz, czz=czz
)

rotor = rs.Rotor(shaft_elem, [disk0, disk1], [bearing0, bearing1])

In [3]:
"""Inserting a mass and phase unbalance and defining the local response."""
mass_unb = [5e-4, 0]
phase_unb = [-np.pi / 2, 0]
node_unb = [12, 24]
probe1 = Probe(14, 0)
probe2 = Probe(22, 0)

In [4]:
"""Calculate the response of the rotor connected by a flexible mechanical coupling with parallel,
angular or combined misalignment."""
results = rotor.run_misalignment(
    coupling="flex",
    mis_type="parallel",  # change here the type: mis_type="angular" or mis_type="combined"
    radial_stiffness=40e3,
    bending_stiffness=38e3,
    mis_distance_x=2e-4,
    mis_distance_y=2e-4,
    mis_angle=5 * np.pi / 180,
    input_torque=0,
    load_torque=0,
    n=0,
    speed=Q_(1200, "RPM"),
    node=node_unb,
    unbalance_magnitude=mass_unb,
    unbalance_phase=phase_unb,
    t=np.arange(0, 5, 0.0001),
    model_reduction={"num_modes": 12},  # Pseudo-modal method, optional
)

In [5]:
"""Plots the time response for the two given probes."""
results.plot_1d([probe1, probe2]).show()

In [6]:
"""Plots the frequency response for the two given probes."""
results.plot_dfft(
    [probe1, probe2], frequency_range=Q_((0, 100), "Hz"), yaxis_type="log"
).show()